In [1]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [2]:
import matplotlib.pyplot as plt
import warnings

plt.style.use('seaborn')
# plt.style.use('seaborn-colorblind') #alternative
plt.rcParams['figure.figsize'] = [8, 4.5]
plt.rcParams['figure.dpi'] = 300
warnings.simplefilter(action='ignore', category=FutureWarning)

# Volatility Forecasting

## Explaining stock returns' volatility with ARCH models

### How to do it...

1. Import the libraries:

In [5]:
import pandas as pd
import yfinance as yf
from arch import arch_model

2. Specify the risky asset and the time horizon:

In [6]:
RISKY_ASSET = 'GOOG'
START_DATE = '2015-01-01'
END_DATE = '2018-12-31'

3. Download data from Yahoo Finance:

In [7]:
df = yf.download(RISKY_ASSET,
                 start=START_DATE,
                 end=END_DATE,
                 adjusted=True)

print(f'Downloaded {df.shape[0]} rows of data.')

[*********************100%***********************]  1 of 1 downloaded
Downloaded 1006 rows of data.


4. Calculate daily returns:

In [8]:
returns = 100 * df['Adj Close'].pct_change().dropna()
returns.name = 'asset_returns'
print(f'Average return: {round(returns.mean(), 2)}%')
returns.plot(title=f'{RISKY_ASSET} returns: {START_DATE} - {END_DATE}');

plt.tight_layout()
# plt.savefig('images/ch5_im1.png')
plt.show()

Average return: 0.08%


5. Specify the ARCH model:

In [9]:
model = arch_model(returns, mean='Zero', vol='ARCH', p=1, o=0, q=0)

6. Estimate the model and print the summary:

In [10]:
model_fitted = model.fit(disp='off')
print(model_fitted.summary())

                        Zero Mean - ARCH Model Results                        
Dep. Variable:          asset_returns   R-squared:                       0.000
Mean Model:                 Zero Mean   Adj. R-squared:                  0.001
Vol Model:                       ARCH   Log-Likelihood:               -1800.60
Distribution:                  Normal   AIC:                           3605.20
Method:            Maximum Likelihood   BIC:                           3615.02
                                        No. Observations:                 1005
Date:                Sun, Jan 19 2020   Df Residuals:                     1003
Time:                        22:10:26   Df Model:                            2
                             Volatility Model                             
                 coef    std err          t      P>|t|    95.0% Conf. Int.
--------------------------------------------------------------------------
omega          1.6323      0.167      9.794  1.196e-22   [  1.30

7. Plot the residuals and the conditional volatility:

In [12]:
model_fitted.plot(annualize='D')

plt.tight_layout()
# plt.savefig('images/ch5_im3.png')
plt.show()

## Explaining stock returns' volatility with GARCH models

### How to do it...

1. Specify the GARCH model:

In [13]:
model = arch_model(returns, mean='Zero', vol='GARCH', 
                   p=1, o=0, q=1)

2. Estimate the model and print the summary:

In [14]:
model_fitted = model.fit(disp='off')
print(model_fitted.summary())

                       Zero Mean - GARCH Model Results                        
Dep. Variable:          asset_returns   R-squared:                       0.000
Mean Model:                 Zero Mean   Adj. R-squared:                  0.001
Vol Model:                      GARCH   Log-Likelihood:               -1764.88
Distribution:                  Normal   AIC:                           3535.76
Method:            Maximum Likelihood   BIC:                           3550.50
                                        No. Observations:                 1005
Date:                Sun, Jan 19 2020   Df Residuals:                     1002
Time:                        22:45:11   Df Model:                            3
                              Volatility Model                             
                 coef    std err          t      P>|t|     95.0% Conf. Int.
---------------------------------------------------------------------------
omega          0.1781      0.157      1.134      0.257    [ -

3. Plot the residuals and the conditional volatility:

In [15]:
model_fitted.plot(annualize='D')

plt.tight_layout()
# plt.savefig('images/ch5_im5.png')
plt.show()

## Implementing CCC-GARCH model for multivariate volatility forecasting

### How to do it...

1. Import the libraries:

In [3]:
import pandas as pd
import yfinance as yf
from arch import arch_model

2. Specify the risky asset and the time horizon:

In [4]:
RISKY_ASSETS = ['GOOG', 'MSFT', 'AAPL']
N = len(RISKY_ASSETS)
START_DATE = '2015-01-01'
END_DATE = '2018-12-31'

3. Download data from Yahoo Finance:

In [5]:
df = yf.download(RISKY_ASSETS,
                 start=START_DATE,
                 end=END_DATE,
                 adjusted=True)

print(f'Downloaded {df.shape[0]} rows of data.')

[*********************100%***********************]  3 of 3 downloaded
Downloaded 1006 rows of data.


4. Calculate daily returns:

In [6]:
returns = 100 * df['Adj Close'].pct_change().dropna()
returns.plot(subplots=True, 
             title=f'Stock returns: {START_DATE} - {END_DATE}')

plt.tight_layout()
# plt.savefig('images/ch5_im6.png')
plt.show()

5. Define lists for storing objects:

In [7]:
coeffs = []
cond_vol = []
std_resids = []
models = []

6. Estimate the univariate GARCH models:

In [8]:
for asset in returns.columns:
    # specify and fit the model
    model = arch_model(returns[asset], mean='Constant', 
                       vol='GARCH', p=1, o=0, q=1).fit(update_freq=0, 
                                                       disp='off');
    # store results in the lists 
    coeffs.append(model.params)
    cond_vol.append(model.conditional_volatility)
    std_resids.append(model.resid / model.conditional_volatility)
    models.append(model)

7. Store the results in DataFrames:

In [9]:
coeffs_df = pd.DataFrame(coeffs, index=returns.columns)
cond_vol_df = pd.DataFrame(cond_vol).transpose() \
                                    .set_axis(returns.columns, 
                                              axis='columns', 
                                              inplace=False)
std_resids_df = pd.DataFrame(std_resids).transpose() \
                                        .set_axis(returns.columns, 
                                                  axis='columns', 
                                                  inplace=False)

In [10]:
coeffs_df

mu     omega  alpha[1]   beta[1]
AAPL  0.123511  0.221315  0.126038  0.784369
GOOG  0.080484  0.193113  0.187870  0.747876
MSFT  0.119715  0.384615  0.253280  0.624706

8. Calculate the constant conditional correlation matrix (R):

In [11]:
R = std_resids_df.transpose() \
                 .dot(std_resids_df) \
                 .div(len(std_resids_df))

9. Calculate the 1-step ahead forecast of the conditional covariance matrix :

In [12]:
# define objects
diag = []
D = np.zeros((N, N))

# populate the list with conditional variances
for model in models:
    diag.append(model.forecast(horizon=1).variance.values[-1][0])
# take the square root to obtain volatility from variance
diag = np.sqrt(np.array(diag))
# fill the diagonal of D with values from diag
np.fill_diagonal(D, diag)

# calculate the conditional covariance matrix
H = np.matmul(np.matmul(D, R.values), D)

In [13]:
H

array([[6.98457361, 3.26885359, 3.73865239],
       [3.26885359, 6.15816116, 4.47315426],
       [3.73865239, 4.47315426, 7.51632679]])

## Forecasting the conditional covariance matrix using DCC-GARCH

### How to do it...

1. Import the libraries:

In [14]:
import pandas as pd

In [15]:
%load_ext rpy2.ipython

2. Install `rmgarch` R package (run only once) and load it:

In [16]:
%%R

#install.packages('rmgarch', repos = "http://cran.us.r-project.org")
library(rmgarch)

R[write to console]: Loading required package: rugarch

R[write to console]: Loading required package: parallel

R[write to console]: Registered S3 method overwritten by 'xts':
  method     from
  as.zoo.xts zoo 

R[write to console]: 
Attaching package: ‘rugarch’


R[write to console]: The following object is masked from ‘package:stats’:

    sigma




3. Import the dataset into R:

In [17]:
%%R -i returns
print(head(returns, 5))

                          AAPL       GOOG       MSFT
2015-01-02 00:00:00 -0.9564189 -0.3028802  0.6714628
2015-01-05 00:00:00 -2.8173221 -2.0845673 -0.9290138
2015-01-06 00:00:00  0.0102438 -2.3162783 -1.4666987
2015-01-07 00:00:00  1.4032572 -0.1717973  1.2689117
2015-01-08 00:00:00  3.8484848  0.3141697  2.9397590


4. Define the model specification:

In [25]:
%%R

# define GARCH(1,1) model
univariate_spec <- ugarchspec(mean.model = list(armaOrder = c(0,0)),
                              variance.model = list(garchOrder = c(1,1), 
                                                    model = "sGARCH"),
                              distribution.model = "norm")

# define DCC(1,1) model
n <- dim(returns)[2]
dcc_spec <- dccspec(uspec = multispec(replicate(n, univariate_spec)),
                    dccOrder = c(1,1),
                    distribution = "mvnorm")

dcc_spec


*------------------------------*
*       DCC GARCH Spec         *
*------------------------------*
Model          :  DCC(1,1)
Estimation     :  2-step
Distribution   :  mvnorm
No. Parameters :  17
No. Series     :  3



5. Estimate the model:

In [ ]:
%%R
dcc_fit <- dccfit(dcc_spec, data=returns)
dcc_fit

6. Calculate the 5-step ahead forecasts:

In [ ]:
forecasts <- dccforecast(dcc_fit, n.ahead = 5)

7. Access the forecasts:

In [ ]:
%%R

# conditional covariance matrix
forecasts@mforecast$H
# conditional correlation matrix
forecasts@mforecast$R
# proxy correlation process
forecasts@mforecast$Q
# conditional mean forecasts
forecasts@mforecast$mu

### There's more

In [ ]:
%%R

# parallelized DCC-GARCH(1,1)

library('parallel')

# set up the cluster
cl <- makePSOCKcluster(3)

# define parallelizable specification
parallel_fit <- multifit(multispec(replicate(n, univariate_spec)), 
                         returns, 
                         cluster = cl)

# fit the DCC-GARCH model
dcc_fit <- dccfit(dcc_spec, 
                  data = returns, 
                  fit.control = list(eval.se = TRUE), 
                  fit = parallel_fit, 
                  cluster = cl)

# stop the cluster
stopCluster(cl)